# link budjet calculator

this code has for purpose to calculate the link budjet <b>between tolosat and the nearest iridium satellite </b> at a given time or a range of time.

---

## libraries import

In [1]:
# general library import
import numpy as np

# TLE tools import
from tletools import TLE

# poly astro library import
from astropy import units as u
import poliastro as pa

# plotting utilities
import plotly.io as pio
from poliastro.plotting import OrbitPlotter3D

# to plot at current time
from astropy.time import Time

__[here is where](http://celestrak.com/NORAD/elements/)__ you can download actual TLE :

if you need a refresh, here's the __[wikipedia page](https://en.wikipedia.org/wiki/Two-line_element_set)__ for TLE

once downloaded, you can load them up with :

```python
TLE.load('TLE_file.txt')
```

In [2]:
# this cell convert list of TLE to list of poliastro.orbit

iridium_TLE = TLE.load('iridiumTLE.txt') # load TLE

iridium_orb = [] # initialization

for i in range(len(iridium_TLE)): # convertion
    iridium_orb.append(iridium_TLE[i].to_orbit())

## plot the iridium constellation

In [3]:
#this cell plot all the iridium constellation (to see what's going on)

pio.renderers.default = "plotly_mimetype+notebook_connected"

frame = OrbitPlotter3D()

now = Time.now() # get the actual time

for i in range(len(iridium_orb)):
    iridium_orb[i] = iridium_orb[i].propagate(now) # propagate the position at given time (now)
    frame.plot(iridium_orb[i], label=iridium_TLE[i].name) # plot

frame.show()


## get the distance between two object

Each orbit has an ```orbit.r``` attribute such has :

``` python
print(iridium_orb[0].r)
```
<blockquote>
>>> [-2266.63314285  2399.00541761  6346.82371324] km
</blockquote>

So the formula is simply :

$ dist_{ab} = \sqrt{(x_a-x_b)^2 + (y_a-y_b)^2 + (z_a-z_b)^2}$

In [4]:
#function to get the distance between two object

def dist_between(a, b):
    return np.sqrt( (a.r[0]-b.r[0])**2 + (a.r[1]-b.r[1])**2 + (a.r[2]-b.r[2])**2)

## tolosat orbital definition

In [5]:
tolosat_orb = pa.twobody.orbit.Orbit.from_classical(
    pa.bodies.Earth,    # main attractor
    6878 * u.km,        # Semi-major axis
    0.002 * u.one,      # Eccentricity
    97.4 * u.deg,       # Inclination
    0.187 * u.rad,      # RAAN (Right ascension of the ascending node)
    np.pi/2 * u.rad,    # Argument of the pericenter
    0 * u.deg,          # true anomaly
    now                 # epoch (time)
)

just for the pleasure, let's see the tolosat orbit

In [6]:
tolosat_plt = OrbitPlotter3D()

tolosat_plt.plot(tolosat_orb,label='tolosat')

tolosat_plt.show()

let's get the distance between tolosat and every iridium satellite now.

In [7]:
distFromConst = []
distFromConst_name = []

for i in range(len(iridium_orb)):
    distFromConst.append(dist_between(tolosat_orb,iridium_orb[i]))
    distFromConst_name.append(iridium_TLE[i].name)

index_of_min = distFromConst.index(min(distFromConst))

print("minimal distance from iridium constellation is :")
print(str(distFromConst[index_of_min]) + " from " + distFromConst_name[index_of_min])

minimal distance from iridium constellation is :
649.9797667184237 km from IRIDIUM 28 [-]
